In [1]:
import uuid
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import my_connector
from datetime import datetime
from my_connector import MySQLConnector

In [2]:
df = pd.read_csv("Datasets/Data_Combinada.csv", low_memory=False)

In [3]:
df.head(10)

num_expediente       fecha     hora  \
0    2022S000001  01/01/2022  1:30:00   
1    2022S000001  01/01/2022  1:30:00   
2    2022S000002  01/01/2022  0:30:00   
3    2022S000002  01/01/2022  0:30:00   
4    2022S000002  01/01/2022  0:30:00   
5    2022S000003  01/01/2022  1:50:00   
6    2022S000003  01/01/2022  1:50:00   
7    2022S000004  01/01/2022  3:40:00   
8    2022S000004  01/01/2022  3:40:00   
9    2022S000005  01/01/2022  4:30:00   

                                 localizacion   numero  cod_distrito  \
0                          AVDA. ALBUFERA, 19       19          13.0   
1                          AVDA. ALBUFERA, 19       19          13.0   
2  PLAZA. CANOVAS DEL CASTILLO / PASEO. PRADO        2           3.0   
3  PLAZA. CANOVAS DEL CASTILLO / PASEO. PRADO        2           3.0   
4  PLAZA. CANOVAS DEL CASTILLO / PASEO. PRADO        2           3.0   
5                      CALL. SAN BERNARDO, 53       53           1.0   
6                      CALL. SAN BERNARDO, 53       53           1.0   
7            CALL. ALCALA / PLAZA. EISENHOWER      728          20.0   
8            CALL. ALCALA / PLAZA. EISENHOWER      728          20.0   
9                        AUTOV. A-42, +00500E  +00500E          12.0   

              distrito                tipo_accidente estado_meteorológico  \
0   PUENTE DE VALLECAS                       Alcance            Despejado   
1   PUENTE DE VALLECAS                       Alcance            Despejado   
2               RETIRO       Colisión fronto-lateral                  NaN   
3               RETIRO       Colisión fronto-lateral                  NaN   
4               RETIRO       Colisión fronto-lateral                  NaN   
5               CENTRO           Atropello a persona            Despejado   
6               CENTRO           Atropello a persona            Despejado   
7  SAN BLAS-CANILLEJAS  Choque contra obstáculo fijo            Despejado   
8  SAN BLAS-CANILLEJAS  Choque contra obstáculo fijo            Despejado   
9                USERA  Choque contra obstáculo fijo            Despejado   

             tipo_vehiculo  ...       rango_edad sexo cod_lesividad  \
0                  Turismo  ...  De 30 a 34 años    M           NaN   
1                  Turismo  ...  De 45 a 49 años    H           NaN   
2  Motocicleta hasta 125cc  ...  De 30 a 34 años    H           NaN   
3  Motocicleta hasta 125cc  ...  De 35 a 39 años    M           NaN   
4                  Turismo  ...  De 40 a 44 años    H           NaN   
5      Motocicleta > 125cc  ...      Desconocido    H           NaN   
6      Motocicleta > 125cc  ...  De 18 a 20 años    M           7.0   
7                  Turismo  ...  De 50 a 54 años    H           2.0   
8                  Turismo  ...  De 55 a 59 años    M           3.0   
9                  Turismo  ...  De 45 a 49 años    H           NaN   

                                           lesividad coordenada_x_utm  \
0                                                NaN       443359,226   
1                                                NaN       443359,226   
2                                                NaN       441155,351   
3                                                NaN       441155,351   
4                                                NaN       441155,351   
5                                                NaN       439995,351   
6  Asistencia sanitaria sólo en el lugar del acci...       439995,351   
7                Ingreso inferior o igual a 24 horas       449693,925   
8                        Ingreso superior a 24 horas       449693,925   
9                                                NaN       438952,303   

  coordenada_y_utm positiva_alcohol  positiva_droga  numero_pasajeros  fugado  
0      4472082,272              0.0             0.0                 2      No  
1      4472082,272              0.0             0.0                 2      No  
2      4474129,588              1.0             0.0                 3      No  
3  

-- Creación de la tabla de Distritos
CREATE TABLE Distritos (
    distrito_id INT PRIMARY KEY,
    codigo_distrito VARCHAR(255),
    nombre_distrito VARCHAR(255)
);

-- Creación de la tabla de Direcciones
CREATE TABLE Direcciones (
    direccion_id INT PRIMARY KEY,
    calle VARCHAR(255),
    numero INT
);

-- Creación de la tabla de Accidentes
CREATE TABLE Accidentes (
    num_expediente VARCHAR(255) PRIMARY KEY,
    fecha DATE,
    hora TIME,
    direccion_id INT,
    distrito_id INT,
    tipo_accidente VARCHAR(255),
    estado_meteorologico VARCHAR(255),
    coordenada_x_utm VARCHAR(255),
    coordenada_y_utm VARCHAR(255),
    positivo_alcohol BOOLEAN,
    positivo_droga BOOLEAN,
    fugado BOOLEAN,
    FOREIGN KEY (direccion_id) REFERENCES Direcciones(direccion_id),
    FOREIGN KEY (distrito_id) REFERENCES Distritos(distrito_id)
);

-- Creación de la tabla de Personas Involucradas en Accidentes
CREATE TABLE PersonasInvolucradas (
    id INT PRIMARY KEY,
    num_expediente VARCHAR(255),
    tipo_vehiculo VARCHAR(255),
    tipo_persona VARCHAR(255),
    rango_edad VARCHAR(255),
    sexo CHAR(1),
    codigo_lesividad INT,
    lesividad VARCHAR(255),
    numero_pasajeros INT,
    FOREIGN KEY (num_expediente) REFERENCES Accidentes(num_expediente)
);


Calculamos el máximo para dimensionar correctamente la base de datos

In [4]:
df['num_expediente'].max()

'2023S029136'

In [19]:
connector = MySQLConnector('localhost', 'root', 'root', 'TNT')
connector.connect()

Connected to MySQL database.


In [11]:
df = df.sort_values(by=['fecha', 'hora']).ffill()
df = df.sort_values(by=['fecha', 'hora']).bfill()
df['fugado'].replace({'No': 0, 'Si': 1}, inplace=True)
df['numero'].fillna('S/N', inplace=True)
df['tipo_vehiculo'].fillna('Desconocido', inplace=True)
df['lesividad'].fillna('Sin asistencia - Desconocido', inplace=True)
df['cod_lesividad'].fillna(0, inplace=True)

In [42]:
fechas = df.drop_duplicates(subset=['fecha', 'estado_meteorológico'])

In [43]:
fechas = fechas.filter(items=['fecha', 'estado_meteorológico'])

In [45]:
fechas.reset_index().pop("index").head(0)

Series([], Name: index, dtype: int64)

In [58]:
fechas['estado_meteorológico'] = fechas['estado_meteorológico'].replace({'Despejado':'D', 'Nublado':'n','Lluvia débil':'l', 'LLuvia intensa':'L', 'Granizando':'G', 'Nevando':'N', 'Se desconoce':'S'})

In [74]:
fechas = fechas.drop_duplicates()

In [76]:
for index, row in fechas.iterrows():
    fechas_query = f"""INSERT INTO Fecha(fecha, weather) VALUES ('{datetime.strptime(row[0], "%d/%m/%Y")}', '{row[1]}')"""
    print(fechas_query)
    connector.execute_query(fechas_query)

/tmp/ipykernel_7986/383714099.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  fechas_query = f"""INSERT INTO Fecha(fecha, weather) VALUES ('{datetime.strptime(row[0], "%d/%m/%Y")}', '{row[1]}')"""


INSERT INTO Fecha(fecha, weather) VALUES ('2022-01-01 00:00:00', 'D')
Query executed successfully.
INSERT INTO Fecha(fecha, weather) VALUES ('2023-01-01 00:00:00', 'n')
Query executed successfully.
INSERT INTO Fecha(fecha, weather) VALUES ('2023-01-01 00:00:00', 'D')
Query executed successfully.
INSERT INTO Fecha(fecha, weather) VALUES ('2023-01-01 00:00:00', 'l')
Query executed successfully.
INSERT INTO Fecha(fecha, weather) VALUES ('2022-02-01 00:00:00', 'D')
Query executed successfully.
INSERT INTO Fecha(fecha, weather) VALUES ('2023-02-01 00:00:00', 'D')
Query executed successfully.
INSERT INTO Fecha(fecha, weather) VALUES ('2022-03-01 00:00:00', 'D')
Query executed successfully.
INSERT INTO Fecha(fecha, weather) VALUES ('2023-03-01 00:00:00', 'D')
Query executed successfully.
INSERT INTO Fecha(fecha, weather) VALUES ('2023-03-01 00:00:00', 'n')
Query executed successfully.
INSERT INTO Fecha(fecha, weather) VALUES ('2022-04-01 00:00:00', 'D')
Query executed successfully.
INSERT INT

In [47]:
cod_distrito_unique = df['cod_distrito'].unique()
distrito_unique = df['distrito'].unique()
emparejados = {cod: dist for cod, dist in zip(cod_distrito_unique, distrito_unique)}

In [7]:
for cod, dist in emparejados.items():
    distrito_query = f"""
        INSERT INTO Distritos (codigo_distrito, nombre_distrito) VALUES ('{cod}', '{dist}')
        """

    connector.execute_query(distrito_query)

distrito_query = f"""
        INSERT INTO Distritos (codigo_distrito, nombre_distrito) VALUES ('0', 'DESCONOCIDO')
        """
connector.execute_query(distrito_query)

Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.


In [15]:
df['localizacion'] = df['localizacion'].str.replace("/", '-').str.replace("'", "")
df['coordenada_y_utm'] = df['coordenada_y_utm'].str.replace(",", '.')
df['coordenada_x_utm'] = df['coordenada_x_utm'].str.replace(",", '.')

In [16]:
accidentes = df.filter(
    items=['num_expediente', 'fecha', 'hora', 'localizacion', 'numero', 'cod_distrito', 'tipo_accidente',
           'estado_meteorológico', 'coordenada_x_utm', 'coordenada_y_utm', 'positiva_alcohol', 'positiva_droga',
           'fugado'])
accidentes.head()

num_expediente       fecha      hora  \
13     2022S000008  01/01/2022   0:25:00   
2      2022S000002  01/01/2022   0:30:00   
3      2022S000002  01/01/2022   0:30:00   
4      2022S000002  01/01/2022   0:30:00   
165    2022S000088  01/01/2022  11:45:00   

                                     localizacion numero  cod_distrito  \
13                            PLAZA. ENCUENTRO, 2      2          14.0   
2      PLAZA. CANOVAS DEL CASTILLO - PASEO. PRADO      2           3.0   
3      PLAZA. CANOVAS DEL CASTILLO - PASEO. PRADO      2           3.0   
4      PLAZA. CANOVAS DEL CASTILLO - PASEO. PRADO      2           3.0   
165  AVDA. VALLADOLID - PLAZA. REPUBLICA DE CHILE     10           9.0   

                   tipo_accidente estado_meteorológico coordenada_x_utm  \
13   Choque contra obstáculo fijo            Despejado       444759.786   
2         Colisión fronto-lateral            Despejado       441155.351   
3         Colisión fronto-lateral            Despejado       441155.351   
4         Colisión fronto-lateral            Despejado       441155.351   
165              Colisión lateral            Despejado       437731.276   

    coordenada_y_utm  positiva_alcohol  positiva_droga  fugado  
13       4472970.631               0.0             0.0       0  
2        4474129.588               1.0             0.0       0  
3        4474129.588               0.0             0.0       0  
4        4474129.588               0.0             0.0       0  
165      4476176.535               0.0             0.0       0

In [17]:
patron = r'\d{2}/\d{2}/\d{4}'

filas_con_formato_incorrecto = df[~df['fecha'].str.match(patron)]

In [18]:
filas_con_formato_incorrecto

Empty DataFrame
Columns: [num_expediente, fecha, hora, localizacion, numero, cod_distrito, distrito, tipo_accidente, estado_meteorológico, tipo_vehiculo, tipo_persona, rango_edad, sexo, cod_lesividad, lesividad, coordenada_x_utm, coordenada_y_utm, positiva_alcohol, positiva_droga, numero_pasajeros, fugado]
Index: []

[0 rows x 21 columns]

In [19]:
accidentes = accidentes.drop_duplicates(subset=['num_expediente'])

In [20]:
i = 0
for index, row in accidentes.iterrows():
    i = i + 1
    try:
        sql = f"""
        INSERT INTO Accidentes (num_expediente, fecha, hora, calle, numero, codigo_distrito, tipo_accidente, estado_meteorologico, coordenada_x_utm, coordenada_y_utm, positivo_alcohol, positivo_droga, fugado)
        VALUES ('{row['num_expediente']}', '{datetime.strptime(row['fecha'], "%d/%m/%Y")}', '{datetime.strptime(row['hora'], "%H:%M:%S")}', '{row['localizacion']}', '{row['numero']}', {row['cod_distrito']}, '{row['tipo_accidente']}', '{row['estado_meteorológico']}', '{float(row['coordenada_x_utm'])}', '{float(row['coordenada_y_utm'])}', {row['positiva_alcohol']}, {row['positiva_droga']}, {row['fugado']});
    """
        print(f"Current row index: {index}, count: {i}")
        connector.execute_query(sql)
    except Exception as e:
        print(e)

Current row index: 13, count: 1
Query executed successfully.
Current row index: 2, count: 2
Query executed successfully.
Current row index: 165, count: 3
Query executed successfully.
Current row index: 74, count: 4
Query executed successfully.
Current row index: 70, count: 5
Query executed successfully.
Current row index: 72, count: 6
Query executed successfully.
Current row index: 33, count: 7
Query executed successfully.
Current row index: 37, count: 8
Query executed successfully.
Current row index: 45, count: 9
Query executed successfully.
Current row index: 43, count: 10
Query executed successfully.
Current row index: 41, count: 11
Query executed successfully.
Current row index: 48, count: 12
Query executed successfully.
Current row index: 16, count: 13
Query executed successfully.
Current row index: 51, count: 14
Query executed successfully.
Current row index: 49, count: 15
Query executed successfully.
Current row index: 0, count: 16
Query executed successfully.
Current row index:

In [21]:
connector.close()

Connection closed.


In [63]:
personas = df.filter(items=['num_expediente', 'tipo_vehiculo', 'tipo_persona', 'rango_edad', 'sexo','cod_lesividad', 'numero_pasajeros'])

In [65]:
personas.sort_values(by=['num_expediente'])

num_expediente            tipo_vehiculo tipo_persona       rango_edad  \
0        2022S000001                  Turismo    Conductor  De 30 a 34 años   
1        2022S000001                  Turismo    Conductor  De 45 a 49 años   
2        2022S000002  Motocicleta hasta 125cc    Conductor  De 30 a 34 años   
3        2022S000002  Motocicleta hasta 125cc     Pasajero  De 35 a 39 años   
4        2022S000002                  Turismo    Conductor  De 40 a 44 años   
...              ...                      ...          ...              ...   
74954    2023S028337                  Turismo    Conductor  De 25 a 29 años   
74958    2023S028341                  Turismo    Conductor  De 35 a 39 años   
74957    2023S028341  Motocicleta hasta 125cc    Conductor  De 30 a 34 años   
74959    2023S028352  Motocicleta hasta 125cc    Conductor  De 40 a 44 años   
74960    2023S029136                  Turismo    Conductor  De 35 a 39 años   

      sexo  cod_lesividad  numero_pasajeros  
0        M            1.0                 2  
1        H            1.0                 2  
2        H           14.0                 3  
3        M           14.0                 3  
4        H           14.0                 3  
...    ...            ...               ...  
74954    H           14.0                 3  
74958    H           14.0                 2  
74957    H            7.0                 2  
74959    H            1.0                 1  
74960    H           14.0                 1  

[74961 rows x 7 columns]

In [71]:
personas['num_ocurrence'] = 0
personas.groupby(['num_expediente', 'tipo_vehiculo','tipo_persona','rango_edad','sexo','cod_lesividad','numero_pasajeros']).count().reset_index()

num_expediente            tipo_vehiculo tipo_persona       rango_edad  \
0        2022S000001                  Turismo    Conductor  De 30 a 34 años   
1        2022S000001                  Turismo    Conductor  De 45 a 49 años   
2        2022S000002  Motocicleta hasta 125cc    Conductor  De 30 a 34 años   
3        2022S000002  Motocicleta hasta 125cc     Pasajero  De 35 a 39 años   
4        2022S000002                  Turismo    Conductor  De 40 a 44 años   
...              ...                      ...          ...              ...   
74810    2023S028337                  Turismo     Pasajero  De 55 a 59 años   
74811    2023S028341  Motocicleta hasta 125cc    Conductor  De 30 a 34 años   
74812    2023S028341                  Turismo    Conductor  De 35 a 39 años   
74813    2023S028352  Motocicleta hasta 125cc    Conductor  De 40 a 44 años   
74814    2023S029136                  Turismo    Conductor  De 35 a 39 años   

      sexo  cod_lesividad  numero_pasajeros  num_ocurrence  
0        M            1.0                 2              1  
1        H            1.0                 2              1  
2        H           14.0                 3              1  
3        M           14.0                 3              1  
4        H           14.0                 3              1  
...    ...            ...               ...            ...  
74810    M           14.0                 3              1  
74811    H            7.0                 2              1  
74812    H           14.0                 2              1  
74813    H            1.0                 1              1  
74814    H           14.0                 1              1  

[74815 rows x 8 columns]

In [72]:
for index, row in personas.iterrows():
    personas_sql = f"""INSERT INTO PersonasInvolucradas(uuid, num_expediente, tipo_vehiculo,tipo_persona,rango_edad,sexo,codigo_lesividad,numero_pasajeros) values ('{uuid.uuid4()}','{row['num_expediente']}', '{row['tipo_vehiculo']}', '{row['tipo_persona']}', '{row['rango_edad']}', '{row['sexo']}', {row['cod_lesividad']}, {row['numero_pasajeros']})"""
    connector.execute_query(personas_sql)

Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed successfully.
Query executed